In [29]:
import pandas as pd
import numpy as np

import json

import urllib.parse

In [30]:
params = {
        "ch.swisstopo.amtliches-strassenverzeichnis": "zip_label = '8302 Kloten'"
    }

print(json.dumps(params))

{"ch.swisstopo.amtliches-strassenverzeichnis": "zip_label = '8302 Kloten'"}


In [31]:
df = pd.read_csv('immoscout24_cleansed_3.csv', delimiter='|')

In [12]:
# test geocoding
import requests

def geocode_addresses(address_list):
    base_url = "https://api3.geo.admin.ch/rest/services/api/SearchServer"
    geocoded_results = []

    for address in address_list:
        params = {
            'searchText': address,
            'type': 'locations',
            'sr': '4326',  # Use WGS84 for global standard latitude and longitude
            'returnGeometry': 'true'
        }
        
        response = requests.get(base_url, params=params)
        
        if response.status_code == 200:
            results = response.json()
            for result in results.get('results', []):
                attrs = result.get('attrs', {})
                geocoded_results.append({
                    'address': address,
                    'latitude': attrs.get('y'),
                    'longitude': attrs.get('x'),
                    'detail': attrs.get('detail')
                })
        else:
            geocoded_results.append({
                'address': address,
                'error': 'Failed to geocode'
            })

    return geocoded_results

# List of addresses to geocode
addresses = [
    "Bundesplatz 3, 3005 Bern",
    "Bahnhofstrasse 33, 8001 Zurich",
    'Moosstrasse 39, 8038 Zürich',
    'Sperletweg 36, 8052 Zürich'
]

# Get the geocoded data
geocoded_addresses = geocode_addresses(addresses)
print(geocoded_addresses)


[{'address': 'Bahnhofstrasse 33, 8001 Zurich', 'latitude': 47.37117385864258, 'longitude': 8.538500785827637, 'detail': 'bahnhofstrasse 33 8001 zuerich 261 zuerich ch zh'}, {'address': 'Moosstrasse 39, 8038 Zürich', 'latitude': 47.33747100830078, 'longitude': 8.529204368591309, 'detail': 'moosstrasse 39 8038 zuerich 261 zuerich ch zh'}, {'address': 'Sperletweg 36, 8052 Zürich', 'latitude': 47.4247932434082, 'longitude': 8.550409317016602, 'detail': 'sperletweg 36 8052 zuerich 261 zuerich ch zh'}]


In [32]:
# try by creating list and tthen merge later on indexposition

import pandas as pd
import requests

def geocode_addresses(address_list):
    base_url = "https://api3.geo.admin.ch/rest/services/api/SearchServer"
    geocoded_results = []

    for address in address_list:
        params = {
            'searchText': address,
            'type': 'locations',
            'sr': '4326',  # Use WGS84 for global standard latitude and longitude
            'returnGeometry': 'true'
        }
        
        response = requests.get(base_url, params=params)
        
        if response.status_code == 200:
            results = response.json()
            for result in results.get('results', []):
                attrs = result.get('attrs', {})
                geocoded_results.append({
                    'address': address,
                    'latitude': attrs.get('y'),
                    'longitude': attrs.get('x'),
                    'detail': attrs.get('detail')
                })
        else:
            geocoded_results.append({
                'address': address,
                'error': 'Failed to geocode'
            })

    return geocoded_results

addresses = df['address'].tolist()
# Create a DataFrame from the list of addresses
df_addresses = pd.DataFrame({'address': addresses})

# Get the geocoded data
geocoded_results = geocode_addresses(addresses)
df_geocoded = pd.DataFrame(geocoded_results)

# Merge the original DataFrame with the geocoded results
df_merged = pd.merge(df_addresses, df_geocoded, on='address', how='left')

# Print the merged DataFrame
print(df_merged)

                               address   latitude  longitude  \
0        In der Looren 56, 8053 Zürich  47.364555   8.597230   
1     Kügeliloostrasse 99, 8046 Zürich  47.415546   8.530204   
2           Wirzenweid 27, 8053 Zürich  47.357121   8.583215   
3                Lyrenweg, 8047 Zürich  47.374352   8.482235   
4                Lyrenweg, 8047 Zürich  47.374283   8.482404   
...                                ...        ...        ...   
6980       Moosstrasse 39, 8038 Zürich  47.337471   8.529204   
6981       Moosstrasse 39, 8038 Zürich  47.337471   8.529204   
6982       Moosstrasse 39, 8038 Zürich  47.337471   8.529204   
6983        Sperletweg 36, 8052 Zürich  47.424793   8.550409   
6984      Feldblumenweg 5, 8048 Zürich  47.382282   8.484338   

                                                 detail  
0       in der looren 56 8053 zuerich 261 zuerich ch zh  
1     kuegeliloostrasse 99 8046 zuerich 261 zuerich ...  
2          wirzenweid 27 8053 zuerich 261 zuerich ch zh  

In [25]:
df_merged.shape

(6985, 4)

In [26]:
# Merge the DataFrames on their indexes
df_merged2 = pd.merge(df, df_merged, left_index=True, right_index=True)

print(df_merged2)

     page                             type  price  \
0       2  4.5 Zimmer, 107m², CHF 3’082.–    3082   
1       2   3.5 Zimmer, 77m², CHF 2’443.–    2443   
2       2  4.5 Zimmer, 150m², CHF 5’850.–    5850   
3       2         5.5 Zimmer, CHF 5’500.–    5500   
4       2     3 Zimmer, 81m², CHF 2’610.–    2610   
..    ...                              ...    ...   
636    43   1.5 Zimmer, 34m², CHF 2’120.–    2120   
637    43     2 Zimmer, 50m², CHF 2’430.–    2430   
638    43     2 Zimmer, 49m², CHF 2’320.–    2320   
639    43         3.5 Zimmer, CHF 2’570.–    2570   
640    43                       CHF 180.–     180   

                            address_x  \
0       In der Looren 56, 8053 Zürich   
1    Kügeliloostrasse 99, 8046 Zürich   
2          Wirzenweid 27, 8053 Zürich   
3               Lyrenweg, 8047 Zürich   
4           Röslistr. 57, 8006 Zürich   
..                                ...   
636       Moosstrasse 39, 8038 Zürich   
637       Moosstrasse 39, 8038 Züri

In [27]:
df_merged2.to_clipboard()

In [33]:
# Save to file
df_merged2.to_csv('immoscout24_geocoded.csv', sep="|", index=False)

In [34]:
df_merged2.to_clipboard()

In [37]:
df_merged3 =df_merged2[df_merged2['latitude'].notna()]
print(df_merged2.shape)
print(df_merged3.shape)

(641, 31)
(637, 31)


In [38]:
# Save to file
df_merged2.to_csv('immoscout24_geocoded_2.csv', sep="|", index=False)

#### stuff

In [21]:
import requests

def geocode_addresses(row):
    base_url = "https://api3.geo.admin.ch/rest/services/api/SearchServer"
    geocoded_results = []

    for address in row['address']:
        params = {
            'searchText': address,
            'type': 'locations',
            'sr': '4326',  # Use WGS84 for global standard latitude and longitude
            'returnGeometry': 'true'
        }
        
        response = requests.get(base_url, params=params)
        
        if response.status_code == 200:
            results = response.json()
            for result in results.get('results', []):
                attrs = result.get('attrs', {})
                row['latitude'] = attrs.get('y')
                row['longitude'] = attrs.get('x')
                row['detail'] = attrs.get('detail')
                
        else:
            row['error'] = 'Failed to geocode'

    return geocoded_results


In [22]:
dfgeo = df.apply(geocode_addresses)

KeyError: 'address'

In [29]:
import requests
import pandas as pd

def geocode_addresses_to_dataframe(row, dataframe):
    base_url = "https://api3.geo.admin.ch/rest/services/api/SearchServer"

    for address in row['address']:
        params = {
            'searchText': address,
            'type': 'locations',
            'sr': '4326',  # Use WGS84 for global standard latitude and longitude
            'returnGeometry': 'true'
        }
        
        response = requests.get(base_url, params=params)
        
        if response.status_code == 200:
            results = response.json()
            for result in results.get('results', []):
                attrs = result.get('attrs', {})
                latitude = attrs.get('y')
                longitude = attrs.get('x')
                detail = attrs.get('detail')
                
                # Append the geocoded data to the dataframe
                dataframe = dataframe.append({
                    'latitude': latitude,
                    'longitude': longitude,
                    'detail': detail
                }, ignore_index=True)
        else:
            # Append an error message to the dataframe
            dataframe = dataframe.append({'error': 'Failed to geocode'}, ignore_index=True)

    return dataframe

# Example usage:


# Create an empty DataFrame to store the geocoded data
geocoded_df = pd.DataFrame(columns=['latitude', 'longitude', 'detail', 'error'])

# Apply the geocode_addresses_to_dataframe function to each row of the DataFrame 'df'
geocoded_df = df.apply(geocode_addresses_to_dataframe, dataframe=geocoded_df, axis=1)

# Print the resulting DataFrame
print(geocoded_df)


## Approach way to slow due to the performance issue likely stems from the fact that you're appending rows to the DataFrame inside a loop. Appending rows to a DataFrame in each iteration of a loop can be slow because it involves creating a new DataFrame each time.

C:\Users\Pierluigi\AppData\Local\Temp\ipykernel_20084\3261182963.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  dataframe = dataframe.append({
C:\Users\Pierluigi\AppData\Local\Temp\ipykernel_20084\3261182963.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  dataframe = dataframe.append({
C:\Users\Pierluigi\AppData\Local\Temp\ipykernel_20084\3261182963.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  dataframe = dataframe.append({
C:\Users\Pierluigi\AppData\Local\Temp\ipykernel_20084\3261182963.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  dataframe = dataframe.append({
C:\Users\Pierluigi\AppData\Local\Temp\ipykernel_

KeyboardInterrupt: 

In [ ]:
print(geocoded_df)

0    Empty DataFrame
Columns: [latitude, longitude,...
1    Empty DataFrame
Columns: [latitude, longitude,...
dtype: object

In [33]:
import requests
import pandas as pd

def geocode_addresses_to_dataframe(row):
    base_url = "https://api3.geo.admin.ch/rest/services/api/SearchServer"
    geocoded_data = []

    for address in row['address']:
        params = {
            'searchText': address,
            'type': 'locations',
            'sr': '4326',  # Use WGS84 for global standard latitude and longitude
            'returnGeometry': 'true'
        }
        
        response = requests.get(base_url, params=params)
        
        if response.status_code == 200:
            results = response.json()
            for result in results.get('results', []):
                attrs = result.get('attrs', {})
                latitude = attrs.get('y')
                longitude = attrs.get('x')
                detail = attrs.get('detail')
                
                # Append the geocoded data to the list
                geocoded_data.append({
                    'latitude': latitude,
                    'longitude': longitude,
                    'detail': detail
                })
        else:
            # Append an error message to the list
            geocoded_data.append({'error': 'Failed to geocode'})

    # Create a DataFrame from the list of dictionaries
    geocoded_df = pd.DataFrame(geocoded_data)
    return geocoded_df

# Apply the geocode_addresses_to_dataframe function to each row of the DataFrame 'df'
geocoded_df = df.apply(geocode_addresses_to_dataframe, axis=1)

# Print the resulting DataFrame
print(geocoded_df)

ConnectionError: ('Connection aborted.', ConnectionResetError(10054, 'An existing connection was forcibly closed by the remote host', None, 10054, None))

In [6]:
# should be same code but split by creating subsets
import requests
import pandas as pd

def geocode_addresses_to_dataframe(row):
    base_url = "https://api3.geo.admin.ch/rest/services/api/SearchServer"
    geocoded_data = []

    for address in row['address']:
        params = {
            'searchText': address,
            'type': 'locations',
            'sr': '4326',  # Use WGS84 for global standard latitude and longitude
            'returnGeometry': 'true'
        }
        
        response = requests.get(base_url, params=params)
        
        if response.status_code == 200:
            results = response.json()
            for result in results.get('results', []):
                attrs = result.get('attrs', {})
                latitude = attrs.get('y')
                longitude = attrs.get('x')
                detail = attrs.get('detail')
                
                # Append the geocoded data to the list
                geocoded_data.append({
                    'latitude': latitude,
                    'longitude': longitude,
                    'detail': detail
                })
        else:
            # Append an error message to the list
            geocoded_data.append({'error': 'Failed to geocode'})

    # Create a DataFrame from the list of dictionaries
    geocoded_df = pd.DataFrame(geocoded_data)
    return geocoded_df



# Split the DataFrame into subsets (here 2 subsets for demonstration)
num_subsets = 8
subset_size = len(df) // num_subsets

geocoded_dfs = []

for i in range(num_subsets):
    start_idx = i * subset_size
    end_idx = start_idx + subset_size if i < num_subsets - 1 else len(df)
    subset_df = df.iloc[start_idx:end_idx]
    
    # Apply the geocode_addresses_to_dataframe function to each row of the subset DataFrame
    try:
        geocoded_df = subset_df.apply(geocode_addresses_to_dataframe, axis=1)
        geocoded_dfs.append(geocoded_df)
    except Exception as e:
        print(f"Error processing subset {i}: {e}")


# Merge the resulting DataFrames from all subsets, skipping empty DataFrames
merged_geocoded_df = pd.concat([df for df in geocoded_dfs if not df.empty], ignore_index=True)

# Print the resulting DataFrame
print(merged_geocoded_df)


KeyboardInterrupt: 

In [ ]:
merged_geocoded_df[:1]

0          latitude  longitude                     ...
dtype: object

In [8]:
import requests
import pandas as pd

def geocode_addresses(df):
    base_url = "https://api3.geo.admin.ch/rest/services/api/SearchServer"
    geocoded_results = []

    for idx, address in df['address'].iteritems():
        params = {
            'searchText': address,
            'type': 'locations',
            'sr': '4326',  # Use WGS84 for global standard latitude and longitude
            'returnGeometry': 'true'
        }
        
        response = requests.get(base_url, params=params)
        
        if response.status_code == 200:
            results = response.json()
            for result in results.get('results', []):
                attrs = result.get('attrs', {})
                geocoded_results.append({
                    'index': idx,
                    'address': address,
                    'latitude': attrs.get('y'),
                    'longitude': attrs.get('x'),
                    'detail': attrs.get('detail')
                })
        else:
            geocoded_results.append({
                'index': idx,
                'address': address,
                'error': 'Failed to geocode'
            })

    # Convert the results to a DataFrame
    geocoded_df = pd.DataFrame(geocoded_results)
    return geocoded_df

# Geocode addresses
geocoded_df = geocode_addresses(df)

# Join geocoded data back to the original DataFrame
df = df.join(geocoded_df.set_index('index'), on=df.index)
print(df)


AttributeError: 'Series' object has no attribute 'iteritems'

In [17]:
import pandas as pd
import requests

def geocode_addresses(df):
    base_url = "https://api3.geo.admin.ch/rest/services/api/SearchServer"
    # Initialize an empty list to store geocoded results
    geocoded_results = []

    for idx, address in df['address'].iteritems():
        params = {
            'searchText': address,
            'type': 'locations',
            'sr': '4326',  # Use WGS84 for global standard latitude and longitude
            'returnGeometry': 'true'
        }
        
        response = requests.get(base_url, params=params)
        
        if response.status_code == 200:
            results = response.json()
            if results['results']:
                # Assuming there's at least one result and taking the first
                result = results['results'][0]
                attrs = result.get('attrs', {})
                geocoded_results.append({
                    'index': idx,
                    'latitude': attrs.get('y'),
                    'longitude': attrs.get('x'),
                    'detail': attrs.get('detail')
                })
            else:
                geocoded_results.append({'index': idx, 'error': 'No results found'})
        else:
            geocoded_results.append({'index': idx, 'error': 'Failed to geocode'})

    # Convert the results to a DataFrame
    geocoded_df = pd.DataFrame(geocoded_results)
    return geocoded_df.set_index('index')



# Geocode addresses
geocoded_df = geocode_addresses(df)

# Join geocoded data back to the original DataFrame using the correct index alignment
df = df.join(geocoded_df)
print(df)

AttributeError: 'Series' object has no attribute 'iteritems'